In [1]:
import re
import sys
import math
import pandas as pd
import mysql.connector
from datetime import date
from sklearn.metrics.pairwise import cosine_similarity
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from Sastrawi.StopWordRemover.StopWordRemoverFactory import StopWordRemoverFactory

In [2]:
connection = mysql.connector.connect(
    host="localhost",
    user="root",
    password="",
    database="bkk"
)

In [3]:
sql = "select `vacancies`.*, (select count(*) from `applicants` where `vacancies`.`id` = `applicants`.`vacancy_id` and `verified` = '1' and `applicants`.`deleted_at` is null) as `applicants_count` from `vacancies` where `deadline` >= '2023-07-20' and `status` = '1' and (`max_applicants` is null and exists (select * from `companies` where `vacancies`.`company_id` = `companies`.`id` and `status` = '1' and `companies`.`deleted_at` is null) or `max_applicants` is not null and (select count(*) from `applicants` where `vacancies`.`id` = `applicants`.`vacancy_id` and `verified` = 1 and `applicants`.`deleted_at` is null) < max_applicants) and exists (select * from `companies` where `vacancies`.`company_id` = `companies`.`id` and `logo` is not null and `companies`.`deleted_at` is null) and not exists (select * from `applicants` where `vacancies`.`id` = `applicants`.`vacancy_id` and `user_id` = '9450d629-7724-4550-9150-f407cbf6e665' and `applicants`.`deleted_at` is null) and not exists (select * from `notified_vacancies` where `vacancies`.`id` = `notified_vacancies`.`vacancy_id` and `user_id` = '9450d629-7724-4550-9150-f407cbf6e665') and `vacancies`.`deleted_at` is null order by `deadline` desc, `updated_at` desc"
#sql = "select * from vacancies"
itemPerPage = 5
page = 1
minWeight = 0.15
keyword = "Operator Produksi"

In [6]:
cursor = connection.cursor()

# Execute a query
cursor.execute(sql)
vacancies = []
for vacancy in cursor.fetchall():
    # vacancy[0] is id
    # vacancy[2] is position
    # vacancy[4] is description
    vacancies.append([vacancy[0], vacancy[2], vacancy[4]])

df = pd.DataFrame(vacancies, columns=["id", "position", "desc"])
df = df.dropna()

df

id  \
0    55c5c66f-20b4-425c-91f2-986b580a659d   
1    68463de1-69aa-4342-ab97-60c374686a82   
2    6e7319fc-0097-46e1-9376-9d6b0a214adc   
3    3a195483-545e-437d-8aee-ffb16d111a9a   
4    1d067f55-9388-4988-a3aa-dae91587e7bd   
..                                    ...   
486  63456554-40cc-4ee0-ad6c-ee3210aeeab2   
487  ebbf8e3d-98bb-4134-84be-3f6d0ab96109   
488  22f7e15c-9bab-405a-a8c8-5718b3fd219d   
489  17fdc2c9-1bb2-4d4e-8628-db438c1c27dd   
490  edafe2e3-6183-4150-a380-39322a20e00a   

                                              position  \
0                                      Finance Manager   
1                                 Sales MT & Institute   
2                  Sales Executive Kalimantan Sulawesi   
3          AREA SALES MANAGER (KEPALA DEPO PURWAKARTA)   
4            Supervisor Sewing Garment (Kota Salatiga)   
..                                                 ...   
486                                       Receptionist   
487  Pusat Logistik Berikat (PLB) Administration St...   
488                                       Staff Import   
489                            Admin / General Affairs   
490                                               batu   

                                                  desc  
0    <p>Our growing hospitality company is seeking ...  
1    <p><strong>Deskripsi Pekerjaan :</strong></p><...  
2    Saat ini kami sedang membangun perusahaan insu...  
3    <p><strong>Persyaratan</strong></p><ul><li>Usi...  
4    <ol><li>Melakukan koordinasi dengan feeder/ope...  
..                                                 ...  
486  <ul><li>Candidate must possess at least Diplom...  
487  <ul><li>Doing data entry through a good admini...  
488  <p><strong>Deskripsi Pekerjaan</strong></p><p>...  
489  <p>Dicari Admin/General Affairs :</p><p>Kualif...  
490                                         <p>asd</p>  

[491 rows x 3 columns]

In [10]:
# menghapus stop words (kata-kata umum yang sering muncul dan biasanya tidak memiliki makna penting dalam analisis teks)
factory = StemmerFactory()
stemmer = factory.create_stemmer()
stopword = StopWordRemoverFactory().create_stop_word_remover()
html_pattern = re.compile('<.*?>')

kalimat = "<p>Hi Friends!</p><p>Kami adalah perusahaan E-commerce dropship yang sedang berkembang. Lokasi kantor kami strategis di Kemayoran Jakarta Pusat.</p><p>Sejak 2015, Slalu.com telah mendukung dan bekerja sama dengan ratusan reseller agar mereka bisa sukses.</p><p>Jika Anda adalah seseorang yang cekatan, disiplin, creative, dan rajin, kami mengundang Anda untuk bergabung.</p><p>Tugas dan tanggung jawab Anda adalah,</p><ul><li>Melakukan penayangan produk baru mulai dari pemfotoan, pembuatan deskripsi produk dan promosi melalui Sosial Media dan Messenger.</li><li>Menginput dan mengelola stok barang inventori</li><li>Membuat konten di IG, Facebook, Tiktok yang bisa mengengage dan build rapport dengan follower.</li><li>Membina komunikasi dengan reseller dan mendapatkan feedback dari mereka untuk diterapkan sebagai perbaikan.</li></ul><p>Kualifikasi yang kami cari adalah sebagai berikut,</p><ul><li>Energik,</li><li>Punya kemampuan komunikasi yang baik,</li><li>Fast Learner, punya Self-Discipline, Creative, Inovatif.</li><li>Punya pengalaman organisasi di Universitas atau di luar pekerjaan (<em>plus point</em>),</li><li>Kemampuan design, fotografi, video editing, atau public speaking (<em>plus point</em>)</li><li>Berpengalaman di bidang online shop, e-commerce (<em>plus point</em>)</li></ul><p>Tunggu apalagi, yuk, klik apply sekarang juga, dan ikut bantu kami membina reseller-reseller baru!</p>"
hasil = stemmer.stem(html_pattern.sub(r' ', kalimat).lower())
print(hasil)

hi friends kami adalah usaha e-commerce dropship yang sedang kembang lokasi kantor kami strategis di mayor jakarta pusat sejak 2015 slalu com telah dukung dan kerja sama dengan ratus reseller agar mereka bisa sukses jika anda adalah orang yang cekat disiplin creative dan rajin kami undang anda untuk gabung tugas dan tanggung jawab anda adalah laku tayang produk baru mulai dari foto buat deskripsi produk dan promosi lalu sosial media dan messenger menginput dan kelola stok barang inventori buat konten di ig facebook tiktok yang bisa mengengage dan build rapport dengan follower bina komunikasi dengan reseller dan dapat feedback dari mereka untuk terap bagai baik kualifikasi yang kami cari adalah bagai ikut energik punya mampu komunikasi yang baik fast learner punya self-discipline creative inovatif punya alam organisasi di universitas atau di luar kerja plus point mampu design fotografi video editing atau public speaking plus point alam di bidang online shop e-commerce plus point tunggu 

In [5]:

for i, kalimat in enumerate(df.iterrows()):
    df.at[i, "desc"] = re.sub('((www\.[^\s]+)|(https?://[^\s]+)|(http?://[^\s]+))', '', df.loc[i, 'desc'])
    df.at[i, "position"] = re.sub('((www\.[^\s]+)|(https?://[^\s]+)|(http?://[^\s]+))', '', df.loc[i, 'position'])
    df.at[i, "desc"] = stemmer.stem(html_pattern.sub(r' ', df.loc[i, 'desc']).lower())
    break
    #df.at[i, "position"] = stemmer.stem(html_pattern.sub(r' ', df.loc[i, 'position']).lower())
    
#dfCombine = df['position'] + " " + df["desc"]

df

id  \
0    55c5c66f-20b4-425c-91f2-986b580a659d   
1    68463de1-69aa-4342-ab97-60c374686a82   
2    6e7319fc-0097-46e1-9376-9d6b0a214adc   
3    3a195483-545e-437d-8aee-ffb16d111a9a   
4    1d067f55-9388-4988-a3aa-dae91587e7bd   
..                                    ...   
486  63456554-40cc-4ee0-ad6c-ee3210aeeab2   
487  ebbf8e3d-98bb-4134-84be-3f6d0ab96109   
488  22f7e15c-9bab-405a-a8c8-5718b3fd219d   
489  17fdc2c9-1bb2-4d4e-8628-db438c1c27dd   
490  edafe2e3-6183-4150-a380-39322a20e00a   

                                              position  \
0                                      Finance Manager   
1                                 Sales MT & Institute   
2                  Sales Executive Kalimantan Sulawesi   
3          AREA SALES MANAGER (KEPALA DEPO PURWAKARTA)   
4            Supervisor Sewing Garment (Kota Salatiga)   
..                                                 ...   
486                                       Receptionist   
487  Pusat Logistik Berikat (PLB) Administration St...   
488                                       Staff Import   
489                            Admin / General Affairs   
490                                               batu   

                                                  desc  
0    our growing hospitality company is seeking a f...  
1    <p><strong>Deskripsi Pekerjaan :</strong></p><...  
2    Saat ini kami sedang membangun perusahaan insu...  
3    <p><strong>Persyaratan</strong></p><ul><li>Usi...  
4    <ol><li>Melakukan koordinasi dengan feeder/ope...  
..                                                 ...  
486  <ul><li>Candidate must possess at least Diplom...  
487  <ul><li>Doing data entry through a good admini...  
488  <p><strong>Deskripsi Pekerjaan</strong></p><p>...  
489  <p>Dicari Admin/General Affairs :</p><p>Kualif...  
490                                         <p>asd</p>  

[491 rows x 3 columns]

In [25]:
vectorizer = TfidfVectorizer()
countVectorizer = CountVectorizer()
tf = countVectorizer.fit_transform(dfCombine)
tfidf_matrix = vectorizer.fit_transform(dfCombine)
new_tfidf_vector_count = countVectorizer.transform([keyword])
new_tfidf_vector = vectorizer.transform([keyword])

In [26]:
print('Jumlah dokumen:', tf.shape[0])
print('Jumlah term:', tf.shape[1])
print('Daftar Term:', countVectorizer.get_feature_names_out())

Jumlah dokumen: 500
Jumlah term: 6430
Daftar Term: ['00' '000' '002' ... 'zero' 'zona' 'zoom']


In [15]:
print('Matriks TF:')
tf_matrix = pd.DataFrame(tf.toarray(), columns=countVectorizer.get_feature_names_out())
tf_matrix

Matriks TF:


00  000  002  004  008  00am  00pm  0234  034  06  ...  yl  yogyakarta  \
0     0    0    0    0    0     0     0     0    0   0  ...   0           0   
1     0    0    0    0    0     0     0     0    0   0  ...   0           0   
2     0    0    0    0    0     0     0     0    0   0  ...   0           0   
3     0    0    0    0    0     0     0     0    0   0  ...   0           0   
4     0    0    0    0    0     0     0     0    0   0  ...   0           0   
..   ..  ...  ...  ...  ...   ...   ...   ...  ...  ..  ...  ..         ...   
486   0    0    0    0    0     0     0     0    0   0  ...   0           0   
487   0    0    0    0    0     0     0     0    0   0  ...   0           0   
488   0    0    0    0    0     0     0     0    0   0  ...   0           0   
489   0    0    0    0    0     0     0     0    0   0  ...   0           0   
490   0    0    0    0    0     0     0     0    0   0  ...   0           0   

     you  your  youtube  yuk  zahir  zero  zona  zoom  
0      0     0        0    0      0     0     0     0  
1      0     0        0    0      0     0     0     0  
2      0     0        0    0      0     0     0     0  
3      0     0        0    0      0     0     0     0  
4      0     0        0    0      0     0     0     0  
..   ...   ...      ...  ...    ...   ...   ...   ...  
486    0     0        0    0      0     0     0     0  
487    0     0        0    0      0     0     0     0  
488    0     0        0    0      0     0     0     0  
489    0     0        0    0      0     0     0     0  
490    0     0        0    0      0     0     0     0  

[491 rows x 6364 columns]

In [17]:
weight_matrix = pd.DataFrame(tfidf_matrix.toarray(), columns=vectorizer.get_feature_names_out())
weight_matrix

00  000  002  004  008  00am  00pm  0234  034   06  ...   yl  \
0    0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
1    0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
2    0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
3    0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
4    0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
..   ...  ...  ...  ...  ...   ...   ...   ...  ...  ...  ...  ...   
486  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
487  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
488  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
489  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   
490  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  0.0  ...  0.0   

     yogyakarta  you  your  youtube  yuk  zahir  zero  zona  zoom  
0           0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
1           0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
2           0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
3           0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
4           0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
..          ...  ...   ...      ...  ...    ...   ...   ...   ...  
486         0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
487         0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
488         0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
489         0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  
490         0.0  0.0   0.0      0.0  0.0    0.0   0.0   0.0   0.0  

[491 rows x 6364 columns]

In [18]:
document_frequencies = tfidf_matrix.astype(bool).sum(axis=0).A1
words = vectorizer.get_feature_names_out()
idf_values = vectorizer.idf_

In [19]:
columnsName = []
totalDocuments = 0

indexColumn = 1
for index in range(len(dfCombine) + len(keyword)):
    if index == len(dfCombine):
        indexColumn = 1
    
    if index < len(dfCombine):
        columnsName.append("Dokumen " + str(indexColumn))
        totalDocuments = totalDocuments + 1

    else:
        columnsName.append("Keyword " + str(indexColumn))
    
    indexColumn = indexColumn + 1
    
columnsName

['Dokumen 1',
 'Dokumen 2',
 'Dokumen 3',
 'Dokumen 4',
 'Dokumen 5',
 'Dokumen 6',
 'Dokumen 7',
 'Dokumen 8',
 'Dokumen 9',
 'Dokumen 10',
 'Dokumen 11',
 'Dokumen 12',
 'Dokumen 13',
 'Dokumen 14',
 'Dokumen 15',
 'Dokumen 16',
 'Dokumen 17',
 'Dokumen 18',
 'Dokumen 19',
 'Dokumen 20',
 'Dokumen 21',
 'Dokumen 22',
 'Dokumen 23',
 'Dokumen 24',
 'Dokumen 25',
 'Dokumen 26',
 'Dokumen 27',
 'Dokumen 28',
 'Dokumen 29',
 'Dokumen 30',
 'Dokumen 31',
 'Dokumen 32',
 'Dokumen 33',
 'Dokumen 34',
 'Dokumen 35',
 'Dokumen 36',
 'Dokumen 37',
 'Dokumen 38',
 'Dokumen 39',
 'Dokumen 40',
 'Dokumen 41',
 'Dokumen 42',
 'Dokumen 43',
 'Dokumen 44',
 'Dokumen 45',
 'Dokumen 46',
 'Dokumen 47',
 'Dokumen 48',
 'Dokumen 49',
 'Dokumen 50',
 'Dokumen 51',
 'Dokumen 52',
 'Dokumen 53',
 'Dokumen 54',
 'Dokumen 55',
 'Dokumen 56',
 'Dokumen 57',
 'Dokumen 58',
 'Dokumen 59',
 'Dokumen 60',
 'Dokumen 61',
 'Dokumen 62',
 'Dokumen 63',
 'Dokumen 64',
 'Dokumen 65',
 'Dokumen 66',
 'Dokumen 67',
 'Do

In [58]:
printDataFrame = pd.DataFrame({
    columnsName[0]: words
})

indexColumnTemp = 0
for indexColumn, columnName in enumerate(columnsName):
    if indexColumn == 0:
        continue
    elif indexColumn > len(dfCombine):
        if indexColumn == len(dfCombine):
            indexColumnTemp = 0
            
        printDataFrame[columnName] = ""
        for word_index, word in enumerate(words):
            printDataFrame.at[word_index, columnName] = new_tfidf_vector_count[indexColumnTemp, word_index]
    else:
        printDataFrame[columnName] = ""
        for word_index, word in enumerate(words):
            printDataFrame.at[word_index, columnName] = tfidf_matrix_count[indexColumnTemp, word_index]
            
    indexColumnTemp += indexColumnTemp

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  printDataFrame[columnName] = ""
C:\Users\Lenovo\AppData\Local\Temp\ipykernel_36772\1397505186.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

KeyboardInterrupt: 

In [80]:
#term frequency
rows = []
for word_index, word in enumerate(words):
    columns = []
    columns.append(word)
    for index in range(len(dataTf)):
        columns.append(dataTf[index][word_index])

    rows.append(columns)
    
tfDataFrame = pd.DataFrame(rows, columns=columnsName)
    
print(tfDataFrame)


NameError: name 'dataTf' is not defined

In [81]:
for word_index, word in enumerate(words):
    print(str(word_index + 1) + ". Word: " + str(word))
    print("   (TF:" + str(document_frequencies[word_index]) + "  IDF:" + str(idf_values[word_index]) + ")")

1. Word: 00
   (TF:62  IDF:3.975691522670545)
2. Word: 000
   (TF:10  IDF:5.720930976263707)
3. Word: 001
   (TF:1  IDF:7.4256790685021326)
4. Word: 002
   (TF:1  IDF:7.4256790685021326)
5. Word: 004
   (TF:2  IDF:7.020213960393968)
6. Word: 008
   (TF:1  IDF:7.4256790685021326)
7. Word: 00am
   (TF:1  IDF:7.4256790685021326)
8. Word: 00pm
   (TF:1  IDF:7.4256790685021326)
9. Word: 0234
   (TF:1  IDF:7.4256790685021326)
10. Word: 034
   (TF:1  IDF:7.4256790685021326)
11. Word: 06
   (TF:2  IDF:7.020213960393968)
12. Word: 07
   (TF:1  IDF:7.4256790685021326)
13. Word: 08
   (TF:10  IDF:5.720930976263707)
14. Word: 0812
   (TF:1  IDF:7.4256790685021326)
15. Word: 09
   (TF:5  IDF:6.3270667798340225)
16. Word: 10
   (TF:33  IDF:4.5924657244459155)
17. Word: 100
   (TF:5  IDF:6.3270667798340225)
18. Word: 105
   (TF:1  IDF:7.4256790685021326)
19. Word: 11
   (TF:7  IDF:6.039384707382242)
20. Word: 1168
   (TF:1  IDF:7.4256790685021326)
21. Word: 12
   (TF:15  IDF:5.346237526822296)
22. Wo

In [82]:
dframeWords = pd.DataFrame(words, columns=["Word"])
dframeDF = pd.DataFrame(document_frequencies, columns=["DF"])
dframeIDF = pd.DataFrame(idf_values, columns=["IDF"])
result = pd.concat([dframeWords, dframeDF, dframeIDF], axis=1, join='inner')
display(result)

Word  DF       IDF
0        00  62  3.975692
1       000  10  5.720931
2       001   1  7.425679
3       002   1  7.425679
4       004   2  7.020214
...     ...  ..       ...
9690    yuk   1  7.425679
9691  zahir   3  6.732532
9692   zero   2  7.020214
9693   zona   2  7.020214
9694   zoom   1  7.425679

[9695 rows x 3 columns]

In [83]:
dframeTFs = pd.DataFrame(dframeWords)
#frames = []

for i, x in enumerate(range(len(tf.toarray()))):
    dframeTF = pd.DataFrame(tf.toarray()[i], columns=["TF Dokumen " + str(i)])
    dframeTFs = pd.concat([dframeTFs, dframeTF], axis=1, join='inner')
    #print(dframeTF)
    
    #if i > 2:
    #    break
    
#concatingFrames = pd.concat(frames, axis=1, join='inner')
#result = pd.concat([dframeWords, concatingFrames], axis=1, join='inner')

print(dframeTFs)

#len(tf.toarray())

KeyboardInterrupt: 

In [25]:
# norm l2
tfidf_matrix.toarray()

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [26]:
new_tfidf_vector.toarray()

array([[0., 0., 0., ..., 0., 0., 0.]])

In [9]:
rows = []
for word_index, word in enumerate(words):
    columns = []
    columns.append(word)
    for index, matrix in enumerate(tfidf_matrix.toarray()):
        columns.append(matrix[word_index])
    
    for index, matrix in enumerate(new_tfidf_vector.toarray()):
        columns.append(matrix[word_index])

    rows.append(columns)
    
tfidfNormL2DataFrame = pd.DataFrame(rows, columns=columnsName)
print(tfidfNormL2DataFrame)

KeyboardInterrupt: 

In [15]:
for doc_index, doc in enumerate(dfCombine):
    print("Document:", doc_index)
    tfidf_values = tfidf_matrix[doc_index].toarray()[0]
    for tfidf_index, tfidf_value in enumerate(tfidf_values):
        if tfidf_value > 0:
            print("  Word:", words[tfidf_index], "  TF-IDF:", tfidf_value)
    print()

Document: 0
  Word: accounting   TF-IDF: 0.09227669860202606
  Word: accountinghaving   TF-IDF: 0.05038924406658931
  Word: accurate   TF-IDF: 0.02865381726594539
  Word: actively   TF-IDF: 0.04430826461961094
  Word: activitysupport   TF-IDF: 0.053299230157839265
  Word: ad   TF-IDF: 0.03883845499434141
  Word: adjustment   TF-IDF: 0.048324576077171784
  Word: administration   TF-IDF: 0.028770517540832513
  Word: advantageshonest   TF-IDF: 0.053299230157839265
  Word: affairs   TF-IDF: 0.03837526791583681
  Word: all   TF-IDF: 0.08599864882276412
  Word: amp   TF-IDF: 0.06901285010282958
  Word: and   TF-IDF: 0.14540889901143952
  Word: ar   TF-IDF: 0.03608975453939511
  Word: asset   TF-IDF: 0.034107109257290276
  Word: attendance   TF-IDF: 0.04106440862006259
  Word: balance   TF-IDF: 0.03577072829465553
  Word: bank   TF-IDF: 0.11603907995155456
  Word: be   TF-IDF: 0.01966285172771706
  Word: between   TF-IDF: 0.037940170535704025
  Word: beverage   TF-IDF: 0.03883845499434141
  W

  Word: 13   TF-IDF: 0.08205032726162542
  Word: 2003   TF-IDF: 0.08652212588282744
  Word: 30   TF-IDF: 0.04281845756766053
  Word: ada   TF-IDF: 0.060286104453682945
  Word: akhir   TF-IDF: 0.07106356609266391
  Word: amp   TF-IDF: 0.07667906181577354
  Word: analisa   TF-IDF: 0.04697660752072413
  Word: anda   TF-IDF: 0.06809793351888234
  Word: aplikasi   TF-IDF: 0.05922231721998393
  Word: asset   TF-IDF: 0.06315976264324417
  Word: asuransi   TF-IDF: 0.05922231721998393
  Word: atas   TF-IDF: 0.047816270632299894
  Word: audit   TF-IDF: 0.054653509076983665
  Word: awal   TF-IDF: 0.0719212988813644
  Word: baik   TF-IDF: 0.062333486510687465
  Word: baiksemua   TF-IDF: 0.0933111238190911
  Word: baru   TF-IDF: 0.04902530789621726
  Word: bawah   TF-IDF: 0.054653509076983665
  Word: bekerja   TF-IDF: 0.028283916217210534
  Word: bekerjasama   TF-IDF: 0.11711533290818493
  Word: berdomisili   TF-IDF: 0.06744950026016237
  Word: berhubungan   TF-IDF: 0.17870261343207522
  Word: berk

  Word: alat   TF-IDF: 0.0976484883511831
  Word: analisis   TF-IDF: 0.11050896165825898
  Word: and   TF-IDF: 0.04810985368390121
  Word: baik   TF-IDF: 0.055685086229813816
  Word: baja   TF-IDF: 0.15458760002927086
  Word: bearing   TF-IDF: 0.17634533936994398
  Word: bekerja   TF-IDF: 0.05053438854899142
  Word: beratmemiliki   TF-IDF: 0.16671738633378155
  Word: berbahasa   TF-IDF: 0.09680034626704882
  Word: breakdownmelakukan   TF-IDF: 0.17634533936994398
  Word: cikarang   TF-IDF: 0.1255284969231066
  Word: corrective   TF-IDF: 0.13379919747793903
  Word: correctivewajib   TF-IDF: 0.17634533936994398
  Word: d3   TF-IDF: 0.06326535769606201
  Word: deskripsi   TF-IDF: 0.06989440889858034
  Word: ditempatkan   TF-IDF: 0.08013386664397629
  Word: fungsi   TF-IDF: 0.10771215001385531
  Word: hasil   TF-IDF: 0.08845624394153037
  Word: hydrolic   TF-IDF: 0.17634533936994398
  Word: inggris   TF-IDF: 0.08965880236494188
  Word: jenis   TF-IDF: 0.1318985470521507
  Word: kertas   TF-

  Word: achievementsrequirements   TF-IDF: 0.25161642925419203
  Word: agency   TF-IDF: 0.1970871557014503
  Word: agents   TF-IDF: 0.21439440934626972
  Word: agentscalculate   TF-IDF: 0.25161642925419203
  Word: analysis   TF-IDF: 0.13315145721306498
  Word: analyze   TF-IDF: 0.14928158701539984
  Word: and   TF-IDF: 0.27458008562369873
  Word: any   TF-IDF: 0.11233614776678708
  Word: bachelor   TF-IDF: 0.08311703165305702
  Word: bonus   TF-IDF: 0.16604236199664588
  Word: calculate   TF-IDF: 0.20464746955831742
  Word: communication   TF-IDF: 0.09070666696793286
  Word: compensation   TF-IDF: 0.1970871557014503
  Word: data   TF-IDF: 0.08517105098584396
  Word: degree   TF-IDF: 0.07934860229262886
  Word: english   TF-IDF: 0.10030725256453384
  Word: excelhave   TF-IDF: 0.22813194940625472
  Word: for   TF-IDF: 0.07862218366032325
  Word: from   TF-IDF: 0.10251985085612009
  Word: good   TF-IDF: 0.2857553875926082
  Word: have   TF-IDF: 0.11205956710747753
  Word: in   TF-IDF: 0.1

  Word: 35   TF-IDF: 0.08749184798475006
  Word: activitiesproficient   TF-IDF: 0.21033202105633356
  Word: age   TF-IDF: 0.1376878655644777
  Word: amp   TF-IDF: 0.16340512459185283
  Word: and   TF-IDF: 0.17214590633718968
  Word: arcgis   TF-IDF: 0.21033202105633356
  Word: at   TF-IDF: 0.07772532147100418
  Word: autocad   TF-IDF: 0.12343903276838318
  Word: bachelor   TF-IDF: 0.06947945849008773
  Word: bpjstktunjangan   TF-IDF: 0.21033202105633356
  Word: candidate   TF-IDF: 0.10220727893493015
  Word: civil   TF-IDF: 0.4037854131043159
  Word: communication   TF-IDF: 0.07582381104127062
  Word: degree   TF-IDF: 0.06632934080525982
  Word: department   TF-IDF: 0.12769530538999124
  Word: design   TF-IDF: 0.11400375994146916
  Word: engineer   TF-IDF: 0.11751716260298492
  Word: english   TF-IDF: 0.0838491636696454
  Word: exploration   TF-IDF: 0.18438095648331276
  Word: for   TF-IDF: 0.06572211058774703
  Word: geothermal   TF-IDF: 0.21033202105633356
  Word: hari   TF-IDF: 0.11

...

  Word: 5r   TF-IDF: 0.08379422524958265
  Word: able   TF-IDF: 0.04955241267231178
  Word: actions   TF-IDF: 0.0865055346363802
  Word: administration   TF-IDF: 0.05961441761460246
  Word: administrative   TF-IDF: 0.06516434924565821
  Word: analyzing   TF-IDF: 0.07478036137745957
  Word: and   TF-IDF: 0.3012968681652946
  Word: applications   TF-IDF: 0.074119317871484
  Word: areacoordinate   TF-IDF: 0.11043953452198835
  Word: arrival   TF-IDF: 0.10013172183032565
  Word: assertive   TF-IDF: 0.11043953452198835
  Word: attention   TF-IDF: 0.06481442650681075
  Word: autocad   TF-IDF: 0.06481442650681075
  Word: bachelor   TF-IDF: 0.03648174451017115
  Word: be   TF-IDF: 0.040742730912869535
  Word: breakdown   TF-IDF: 0.09681334732804289
  Word: cikarang   TF-IDF: 0.07861454586191109
  Word: collecting   TF-IDF: 0.08807235405216507
  Word: continuous   TF-IDF: 0.08150184582640121
  Word: corrective   TF-IDF: 0.08379422524958265
  Word: culture   TF-IDF: 0.08982390913866294
  Word: d

  Word: 35   TF-IDF: 0.08143783008799627
  Word: amp   TF-IDF: 0.05069942354072675
  Word: baik   TF-IDF: 0.06182141040604306
  Word: baikdapat   TF-IDF: 0.15083726016067425
  Word: bawah   TF-IDF: 0.10840904957881019
  Word: bekerja   TF-IDF: 0.0561031217804417
  Word: berkomunikasi   TF-IDF: 0.09086516712849729
  Word: bertanggung   TF-IDF: 0.07789612933643943
  Word: bertempat   TF-IDF: 0.18508912637447494
  Word: bogor   TF-IDF: 0.13785453131172837
  Word: bpjs   TF-IDF: 0.10988768735918641
  Word: cepat   TF-IDF: 0.1070089614890632
  Word: coaching   TF-IDF: 0.14095954294416987
  Word: dapat   TF-IDF: 0.09037696559405249
  Word: dipersilakan   TF-IDF: 0.1592323786427802
  Word: disiplin   TF-IDF: 0.09601875306484325
  Word: ga   TF-IDF: 0.12352367054025032
  Word: gapendidikan   TF-IDF: 0.18508912637447494
  Word: hr   TF-IDF: 0.21977537471837283
  Word: inisiatif   TF-IDF: 0.11255279627857308
  Word: inovatif   TF-IDF: 0.13256442446206393
  Word: internal   TF-IDF: 0.094561911176

  Word: amp   TF-IDF: 0.04369392476304387
  Word: and   TF-IDF: 0.04603117740983129
  Word: at   TF-IDF: 0.12470077754367252
  Word: bachelor   TF-IDF: 0.055735649162026696
  Word: candidate   TF-IDF: 0.0819895428709389
  Word: cash   TF-IDF: 0.10123971570440338
  Word: chain   TF-IDF: 0.10066450809177077
  Word: courier   TF-IDF: 0.1595140496176912
  Word: customer   TF-IDF: 0.07109388844653211
  Word: degree   TF-IDF: 0.05320865977672928
  Word: description   TF-IDF: 0.07319754907510165
  Word: diploma   TF-IDF: 0.08408016505603498
  Word: driver   TF-IDF: 0.11757781388061907
  Word: drivingmanaging   TF-IDF: 0.16872600892259798
  Word: effective   TF-IDF: 0.1030582449711596
  Word: efficient   TF-IDF: 0.12148216358097319
  Word: engineering   TF-IDF: 0.08174123999365128
  Word: equivalent   TF-IDF: 0.09605379619864717
  Word: experience   TF-IDF: 0.10462435048655715
  Word: field   TF-IDF: 0.07423831823934837
  Word: fleet   TF-IDF: 0.15297806047538973
  Word: for   TF-IDF: 0.052721

  Word: 00   TF-IDF: 0.09176997569410096
  Word: 26   TF-IDF: 0.10026148908063078
  Word: administrasi   TF-IDF: 0.06670572316692266
  Word: alat   TF-IDF: 0.08612250629952897
  Word: awal   TF-IDF: 0.11333293361375622
  Word: baikbersedia   TF-IDF: 0.1147778270955655
  Word: bekerja   TF-IDF: 0.04456953988372343
  Word: berkoordinasi   TF-IDF: 0.09279177097041656
  Word: bertanggung   TF-IDF: 0.06188237896698344
  Word: bulanan   TF-IDF: 0.08167900983003426
  Word: data   TF-IDF: 0.0526463338001648
  Word: dibidang   TF-IDF: 0.08327846230757116
  Word: dinas   TF-IDF: 0.10102312388258554
  Word: dipersilahkan   TF-IDF: 0.10438112370135622
  Word: disukaimampu   TF-IDF: 0.1410140020571097
  Word: excell   TF-IDF: 0.11982839937128736
  Word: external   TF-IDF: 0.0912771847491966
  Word: form   TF-IDF: 0.1062863137090357
  Word: fresh   TF-IDF: 0.07557733135807433
  Word: graduate   TF-IDF: 0.07775830424041716
  Word: hasil   TF-IDF: 0.07801527248112101
  Word: hiring   TF-IDF: 0.2239626

  Word: 30   TF-IDF: 0.07211354657388352
  Word: accounting   TF-IDF: 0.14389425848388146
  Word: accurate   TF-IDF: 0.08936426748421454
  Word: akuntansimenyediakan   TF-IDF: 0.1571517624789839
  Word: amp   TF-IDF: 0.04304684949440913
  Word: ataupun   TF-IDF: 0.10091875525927597
  Word: bagi   TF-IDF: 0.1571517624789839
  Word: bawah   TF-IDF: 0.09204578109852185
  Word: bekerja   TF-IDF: 0.09526982639197724
  Word: berdomisili   TF-IDF: 0.11359640105462454
  Word: bisa   TF-IDF: 0.09417911152532153
  Word: dapat   TF-IDF: 0.15347092191544878
  Word: data   TF-IDF: 0.05626720731693551
  Word: diatas   TF-IDF: 0.1416370297025396
  Word: dibutuhkan   TF-IDF: 0.09509283137320666
  Word: diutamakan   TF-IDF: 0.14592942967108544
  Word: excel   TF-IDF: 0.11907995300653301
  Word: jauh   TF-IDF: 0.13519783380902464
  Word: jawab   TF-IDF: 0.05385139055503677
  Word: kasih   TF-IDF: 0.15071256658546894
  Word: kemayoran   TF-IDF: 0.14571793822006168
  Word: keuanganmembuat   TF-IDF: 0.1381

In [84]:
similarity_scores = cosine_similarity(new_tfidf_vector, tfidf_matrix)

vacanciesWeighted = similarity_scores[0]                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
sortedIndexVacancies = vacanciesWeighted.argsort()[::-1]


In [85]:
pd.DataFrame(vacanciesWeighted, columns=["Skor"])

Skor
0      0.0
1      0.0
2      0.0
3      0.0
4      0.0
...    ...
1229   0.0
1230   0.0
1231   0.0
1232   0.0
1233   0.0

[1234 rows x 1 columns]

In [17]:
for item in vacanciesWeighted:
    print(item)

0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.052429419450565486
0.0
0.10777357311172761
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.13059113972952704
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.06253194741894894
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.03713083086108484
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.03713083086108484
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.03805630113055049
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.03826387167215586
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.10072950019944671
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.053507852480445726
0.0
0.0
0.0
0.04612693973692178
0.0
0.0
0.04612693973692178
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.

In [12]:
# eliminate minimum weight
for index, vacancyScore in enumerate(vacanciesWeighted[sortedIndexVacancies]):
    if(vacancyScore < minWeight):
        # delete element from index 0 to index (but not including this index less than minWeight)
        sortedIndexVacancies = sortedIndexVacancies[0:index]
        break

In [13]:
data = []
pages = math.ceil(len(sortedIndexVacancies) / itemPerPage)
if page == 1 or page == 0:
    start_index = 0
    end_index = itemPerPage
else:
    start_index = (page - 1) * itemPerPage
    if page >= pages:
        end_index = len(sortedIndexVacancies)
    else:
        end_index = page * itemPerPage

for index in sortedIndexVacancies[start_index:end_index]:
    data.append({
        "id": vacancies[index][0],
        "score": vacanciesWeighted[index]
    })

print(data)

[{'id': '9ef5de27-c735-4b11-bea2-055585845097', 'score': 0.4728469642369735}, {'id': 'a5611c0c-cb3a-4133-b1d7-c4b91d067b60', 'score': 0.3953832120382663}, {'id': 'da4057bf-22d4-4ba8-bbc7-edf919cd2ff8', 'score': 0.36336166071043113}, {'id': '9b9f7416-b949-4934-b8af-53c93b6d7af0', 'score': 0.33115689885026073}, {'id': '7ac16a9f-d4e8-457c-8ae7-5ee5829297c8', 'score': 0.32066646542836313}]
